# Adattamento e sovraadattamento di modelli parametrici
### liberamente tratto da ipython interactive computing and visualization, cap. 8

In [ ]:
import numpy as np
import scipy.stats as st
import sklearn.linear_model as lm
import matplotlib.pyplot as plt
%matplotlib inline

Dopo aver caricato le necessarie librerie andiamo a definire una funzione che rappresenti un modello non lineare, per esempio una funzione esponenziale, sulla base della quale genereremo una serie di valori che simulino un esperimento, aggiungendo del rumore gaussiano:

In [ ]:
f= lambda x: np.exp(3*x)

x_tr=np.linspace(0.,1.2, 100)
y_tr=f(x_tr)

x=np.array([0., .1, .2, .5, .8, .9, 1.0])
y=f(x)+np.random.randn(len(x))

In [ ]:
plt.plot(x_tr, y_tr, '--k')
plt.plot(x,y, 'or')

adesso usiamo scikit-learn per adattare un modello lineare sui dati, tramite la classe lm.LinearRegression

In [ ]:
regr=lm.LinearRegression()
regr.fit(x[:,np.newaxis],y)
y_regr=regr.predict(x_tr[:,np.newaxis])

la regressione multivariata prende un insieme di colonne e le usa sulla base del modello per stimare dei parametri. la sintassi sintetica x[:, np.newaxis] genera proprio una matrice, di cui x costituisce la prima colonna, cioè promuove x da vettore a matrice.
il metodo LinearRegression.predict fornisce la predizione di y sulla base del modello con i parametri ottenuti da regr.fit


In [ ]:
plt.plot(x_tr, y_tr, '--k')
plt.plot(x_tr, y_regr, 'g')
plt.plot(x, y, 'or')



abbastanza evidentemente un modello lineare non si adatta molto bene ai nostri dati, proviamo ad adattarvi dei modelli polinomiali di grado 2 e 5. la funzione np.vander ci aiuta a generare le colonne delle potenze di x


In [ ]:
plt.plot(x_tr, y_tr, '--k')
for deg in [2, 5]:
  xs=np.vander(x, deg+1)
  regr.fit(xs, y)
  y_regr=regr.predict(np.vander(x_tr, deg+1))
  plt.plot(x_tr, y_regr, label='grado %d'%(deg))
  print(' '.join(['%.2f' % c for c in regr.coef_]))

plt.legend()
plt.plot(x, y, 'or')

  

il polinomio di grado 2 non passa bene attraverso i punti sperimentali; il polinomio di grado 5 passa attraverso tutti i punti con precisione ma rappresenta un caso di sovraadattamento, dipendentemente dal rumore casuale che abbiamo aggiunto oscillerà in maniera più o meno evidente. un sintomo del sovraadattamento si presenta nell'ampiezza eccessiva dei coefficienti del polinomio con una grande instabilità a piccole deviazioni dei dati sperimentali

uno dei modi per regolarizzare la regressione è aggiungere un termine alla minimizzazione dei minimi quadrati che eviti coefficienti troppo grandi, il più popolare di questi metodi è la ridge regression, che contiene un parametro peso per tale fattore di regolarizzazione. questo parametro è noioso da determinare, di solito per tentativi. scikit-learn offre un metodo di validazione automatico che partiziona i dati in modi diversi per la ridge regression, la classe di riferimento è lm.RidgeCV.

In [ ]:
ridge=lm.RidgeCV()
plt.plot(x_tr, y_tr, '--k')
for deg in [2, 5]:
  xs=np.vander(x, deg+1)
  ridge.fit(xs, y)
  y_ridge=ridge.predict(np.vander(x_tr, deg+1))
  plt.plot(x_tr, y_ridge, label='grado %d'%(deg))
  print('coefficienti per il grado %d: '%(deg)+' '.join(['%.2f' % c for c in ridge.coef_]))

plt.legend()
plt.plot(x, y, 'or')


ora i coefficienti polinomiali sono molto più piccoli e le oscillazioni molto più ridotte, risultando in un'aderenza al modello superiore anche fuori dall'intervallo dei dati sperimentali.
